# copied from a previous rawnav repo - needs to be updated for the new workflow

In [1]:
import os, sys, glob, pandas as pd, geopandas as gpd
import pyarrow as pa, pyarrow.parquet as pq
import folium
from folium.plugins import MarkerCluster
from folium import CircleMarker
from IPython.display import IFrame

#### ben imports
import json
import numpy as np
from scipy.spatial import cKDTree
from shapely.geometry import LineString, Point


pd.set_option('display.max_columns', None)
if not sys.warnoptions:
    import warnings
    warnings.simplefilter("ignore")
%load_ext autoreload
%autoreload 2

#NAD83 Maryland (ft)
wmata_crs = 2248

#os.path.pardir is equivalent to ".."
#need to append folder 2 levels up in order to load wmatarawnav
sys.path.append(os.path.join( os.path.pardir,os.path.pardir))
import wmatarawnav as wr

In [4]:
# 1.2 Set Global Parameters
############################################
if os.getlogin() == "WylieTimmerman":
    path_working = r"C:\OD\OneDrive - Foursquare ITP\Projects\WMATA_AVL"
    os.chdir(os.path.join(path_working))
    sys.path.append(r"C:\OD\OneDrive - Foursquare ITP\Projects\WMATA_AVL")
    path_sp = r"C:\Users\WylieTimmerman\Documents\projects_local\wmata_avl_local"
    path_source_data = os.path.join(path_sp,"data","00-raw")
    path_processed_data = os.path.join(path_sp, "data","02-processed")
    path_segments = os.path.join(path_working,"data","02-processed")
elif os.getlogin() == "abibeka":
    path_working = r"C:\Users\abibeka\OneDrive - Kittelson & Associates, Inc\Documents\Github\WMATA_AVL"
    os.chdir(os.path.join(path_working))
    sys.path.append(path_working)
    path_source_data = r"C:\Users\abibeka\OneDrive - Kittelson & Associates, Inc\Documents\WMATA-AVL\Data"
    path_processed_data = os.path.join(path_source_data, "ProcessedData")
    path_segments = path_processed_data
elif os.getlogin() == "E048374":
    # Working Paths
    path_working = r"C:\Users\E048374\OneDrive - WMATA\rawnav_rachel_fork\WMATA_AVL"
    os.chdir(os.path.join(path_working))
    sys.path.append(r"C:\Users\E048374\OneDrive - WMATA\rawnav_rachel_fork\WMATA_AVL")
    path_source_data = r"\\l-600730\RawNavArchive"
    path_sp = r"C:\Users\E048374\Documents\RawNav"
    path_processed_data = os.path.join(path_sp, "data", "02-processed")
    path_segments = path_processed_data
    
else:
    raise FileNotFoundError("Define the path_working, path_source_data, gtfs_dir, \
                            ZippedFilesloc, and path_processed_data in a new elif block")

### DB connection details

In [2]:
import cx_Oracle

In [3]:
#below is a lazy way to modify the PATH
os.environ['PATH'] = 'C:\\Users\\E048374\\Anaconda3\\envs\\ox;C:\\Users\\E048374\\Anaconda3\\envs\\ox\\Library\\mingw-w64\\bin;C:\\Users\\E048374\\Anaconda3\\envs\\ox\\Library\\usr\\bin;C:\\Users\\E048374\\Anaconda3\\envs\\ox\\Library\\bin;C:\\Users\\E048374\\Anaconda3\\envs\\ox\\Scripts;C:\\Users\\E048374\\Anaconda3\\envs\\ox\\bin;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3\\Library\\mingw-w64\\bin;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3\\Library\\usr\\bin;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3\\Library\\bin;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3\\Scripts;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3\\bin;C:\\;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\Users\\E048374\\Anaconda3\\Scripts\\condabin;C:\\Users\\E048374\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\mingw64\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\usr\\local\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\usr\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\usr\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\mingw64\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\usr\\bin;C:\\Users\\E048374\\bin;C:\\Program Files (x86)\\Common Files\\Oracle\\Java\\javapath;C:\\oracle\\instantclient_19_6;C:\\WINDOWS\\system32;C:\\WINDOWS;C:\\WINDOWS\\System32\\Wbem;C:\\WINDOWS\\System32\\WindowsPowerShell\\v1.0;C:\\WINDOWS\\System32\\OpenSSH;C:\\Program Files\\Docker\\Docker\\resources\\bin;C:\\ProgramData\\DockerDesktop\\version-bin;C:\\Users\\E048374\\Anaconda3;C:\\Users\\E048374\\Anaconda3\\Library\\mingw-w64\\bin;C:\\Users\\E048374\\Anaconda3\\Library\\usr\\bin;C:\\Users\\E048374\\Anaconda3\\Library\\bin;C:\\Users\\E048374\\Anaconda3\\Scripts;C:\\Users\\E048374\\AppData\\Local\\Microsoft\\WindowsApps;C:\\Users\\E048374\\AppData\\Local\\Programs\\Microsoft VS Code\\bin;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\cmd;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\usr\\bin\\vendor_perl;C:\\Users\\E048374\\AppData\\Local\\Programs\\Git\\usr\\bin\\core_perl'

dsn_tns = cx_Oracle.makedsn('XXX', 
                            '1521', 
                            service_name='XXX') 

conn = cx_Oracle.connect(user='XXX', 
                         password='XXX', 
                         dsn=dsn_tns)

## grab roadway links for `H801` and `H802`

In [5]:
#link attributes in `road_link_attributes`
query = """
select 
road.*
,fnodes.latitude from_latitude
,fnodes.longitude from_longitude
,tnodes.latitude to_latitude
,tnodes.longitude to_longitude
from bus_net_link_road road
join bus_net_link_road_nodes fnodes on (fnodes.node_id = road.from_node)
join bus_net_link_road_nodes tnodes on (tnodes.node_id = road.to_node)
where road.pattern_id in ('S401','S402')
"""
road_links = pd.read_sql(query, conn)

In [6]:
road_links.shape

(381, 14)

In [7]:
road_links.head()

PATTERN_ID  FROM_GEOID  FROM_STOP_SEQ  TO_STOP_SEQ  TO_GEOID   FROM_NODE  \
0       S401       21786             48           49     21795    49764271   
1       S402        5947              6            7      5960    49793729   
2       S402        5960              7            8      5948  1381307999   
3       S401       11785             47           48     21786  7597212200   
4       S402        5948              8            9     11816    49764296   

    TO_NODE    LINK_CODE            EDGE_CODE   LENGTH  FROM_LATITUDE  \
0  49745632  21786-21795    49764271-49745632  146.048      38.900207   
1  49745636    5947-5960    49793729-49745636  201.298      38.901336   
2  49764296    5960-5948  1381307999-49764296   82.304      38.901335   
3  49793759  11785-21786  7597212200-49793759   67.429      38.901941   
4  49793759   5948-11816    49764296-49793759  169.003      38.901335   

   FROM_LONGITUDE  TO_LATITUDE  TO_LONGITUDE  
0      -77.033638    38.900209    -77.031950  
1      -77.029624    38.901336    -77.031951  
2      -77.033642    38.901335    -77.034593  
3      -77.036543    38.901334    -77.036546  
4      -77.034593    38.901334    -77.036546

## just take `S402` for testing
S402 is northbound

In [8]:
s402_df = road_links.query("PATTERN_ID == 'S402'").copy()

In [9]:
s402_df

PATTERN_ID  FROM_GEOID  FROM_STOP_SEQ  TO_STOP_SEQ  TO_GEOID   FROM_NODE  \
1         S402        5947              6            7      5960    49793729   
2         S402        5960              7            8      5948  1381307999   
4         S402        5948              8            9     11816    49764296   
5         S402        5960              7            8      5948    49745636   
6         S402        5960              7            8      5948   641116196   
..         ...         ...            ...          ...       ...         ...   
375       S402       11847             53           54     11848   448034306   
376       S402       11847             53           54     11848  5457816524   
377       S402       11847             53           54     11848    49170395   
378       S402       11848             54           55     22079  5457815320   
379       S402       11848             54           55     22079  7111763924   

        TO_NODE    LINK_CODE              EDGE_CODE   LENGTH  FROM_LATITUDE  \
1      49745636    5947-5960      49793729-49745636  201.298      38.901336   
2      49764296    5960-5948    1381307999-49764296   82.304      38.901335   
4      49793759   5948-11816      49764296-49793759  169.003      38.901335   
5     641116196    5960-5948     49745636-641116196   64.625      38.901336   
6    1381307999    5960-5948   641116196-1381307999   81.724      38.901335   
..          ...          ...                    ...      ...            ...   
375  2591082916  11847-11848   448034306-2591082916  139.125      38.992164   
376  5457815320  11847-11848  5457816524-5457815320   54.923      38.992968   
377  5457816524  11847-11848    49170395-5457816524   14.897      38.992907   
378  7111763924  11848-22079  5457815320-7111763924   19.950      38.993203   
379  7111763928  11848-22079  7111763924-7111763928   22.583      38.993292   

     FROM_LONGITUDE  TO_LATITUDE  TO_LONGITUDE  
1        -77.029624    38.901336    -77.031951  
2        -77.033642    38.901335    -77.034593  
4        -77.034593    38.901334    -77.036546  
5        -77.031951    38.901335    -77.032697  
6        -77.032697    38.901335    -77.033642  
..              ...          ...           ...  
375      -77.036142    38.992629    -77.034673  
376      -77.033555    38.993203    -77.032996  
377      -77.033709    38.992968    -77.033555  
378      -77.032996    38.993292    -77.032795  
379      -77.032795    38.993393    -77.032569  

[196 rows x 14 columns]

### split out `from_nodes` and `to_nodes`
for testing below, we only use `from_nodes`

In [10]:
s402_from_nodes = s402_df[['PATTERN_ID','FROM_NODE','FROM_LATITUDE','FROM_LONGITUDE']].reset_index(drop=True).copy()
s402_to_nodes = s402_df[['PATTERN_ID','TO_NODE','TO_LATITUDE','TO_LONGITUDE']].reset_index(drop=True).copy()

In [11]:
s402_from_nodes.loc[:,'geometry'] = s402_from_nodes.loc[:,['FROM_LONGITUDE','FROM_LATITUDE']].apply(lambda x:
                                                                                                   Point(x['FROM_LONGITUDE'],
                                                                                                        x['FROM_LATITUDE']),
                                                                                                   axis=1)

In [12]:
s402_from_nodes_geo = gpd.GeoDataFrame(s402_from_nodes, crs="EPSG:4326", geometry='geometry')

### need to change coordinate reference system to wmata - NAD83 Maryland ft in order to find nearest below

In [13]:
s402_from_nodes_geo.to_crs(wmata_crs, inplace=True)

In [14]:
s402_from_nodes_geo.reset_index(inplace=True, drop=True)

In [15]:
from_nodesA = np.array(list(zip(s402_from_nodes_geo.geometry.x, s402_from_nodes_geo.geometry.y)))

# get cleaned `s4` data

### select one run for analysis

In [158]:
one_rawnav_run = rawnav_qjump_gdf.loc[(rawnav_qjump_gdf.loc[:,'route_pattern']=='   H802')&
                     (rawnav_qjump_gdf.loc[:,'index_run_start']==1494)&
                     (rawnav_qjump_gdf.loc[:,'filename']=='rawnav02833191007.txt')
                     ,:].reset_index(drop=True)

In [228]:
wmata_schedule_dat = (pd.read_csv(os.path.join(path_demo_data,"02_notebook_data","wmata_schedule_data_q_jump_routes.csv"),
                                 index_col = 0)
                      .reset_index(drop=True))

wmata_schedule_gdf = gpd.GeoDataFrame(
            wmata_schedule_dat, 
            geometry = gpd.points_from_xy(wmata_schedule_dat.stop_lon,wmata_schedule_dat.stop_lat),
            crs='EPSG:4326').\
            to_crs(epsg=wmata_crs)

wmata_schedule_dat.head(2)

pattern_id                        pattern_name direction  trip_length  \
0        1236  [64]GEORGIA + PETWOTH - FT TOTTEN      NORTH        11593   
1        1236  [64]GEORGIA + PETWOTH - FT TOTTEN      NORTH        11593   

  route  pattern   pattern_destination                 route_text  route_key  \
0    64        1  NORTH to FORT TOTTEN  Fort Totten-Petworth Line        290   
1    64        1  NORTH to FORT TOTTEN  Fort Totten-Petworth Line        290   

   direction_id  geo_id  stop_id  dist_from_previous_stop  order  \
0           0.0   16808    42582                        0      2   
1           0.0   13092    12882                     1184      3   

   stop_sort_order  assoc_tpid                     geo_description ta_geo_id  \
0                1       134.0  NEW HAMPSHIRE AVE NW + GEORGIA AVE   1002981   
1                2         NaN     NEW HAMPSHIRE AVE + RANDOLPH ST   1003054   

    stop_lon   stop_lat  stop_heading                    geometry  
0 -77.024553  38.935780         18.33  POINT (-77.02455 38.93578)  
1 -77.022461  38.938625         28.05  POINT (-77.02246 38.93863)

### merge one run with stop information
this script finds the nearest point to each stop along the scheduled route

In [257]:
%autoreload 2
stop_summary, stop_index = \
    wr.merge_rawnav_wmata_schedule(
        analysis_route_=analysis_routes,
        analysis_day_=analysis_days,
        rawnav_dat_=one_rawnav_run,
        rawnav_sum_dat_=rawnav_summary_dat,
        wmata_schedule_dat_=wmata_schedule_gdf)

deleted 0 rows of 37 rows with distance to the nearest stop > 100 ft. from index table
deleted 0 of 37 stops with incorrect order from index table


### make a line between stop and nearest rawnav point

In [252]:
esri_imagery = "https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}"
esri_attribution = \
    "Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, " \
    "UPR-EGP, and the GIS User Community"
this_map2 = folium.Map(tiles='cartodbdark_matter', zoom_start=16, max_zoom=25, control_scale=True)
folium.TileLayer(name="EsriImagery", tiles=esri_imagery, attr=esri_attribution,
                 zoom_start=16, max_zoom=25, control_scale=True).add_to(this_map2)
folium.TileLayer('cartodbpositron', zoom_start=16, max_zoom=20, control_scale=True).add_to(this_map2)
folium.TileLayer('openstreetmap', zoom_start=16, max_zoom=20, control_scale=True).add_to(this_map2)

In [258]:
geometry = stop_index.loc[:,
                        ['stop_lat','stop_lon'
                          ,'lat','long']].apply(
                    lambda x: LineString([Point(x['long'],x['lat'])
                  ,Point(x['stop_lon'],x['stop_lat'])])
                , axis=1).tolist()
stop_index_line = gpd.GeoDataFrame(stop_index, crs="EPSG:4326",geometry=geometry)

In [259]:
folium.Choropleth(
    stop_index_line,
    line_weight=3,
    line_color='red'
).add_to(this_map2)

In [260]:
this_map2

In [230]:
stop_index_line = wr.make_target_rawnav_linestring(stop_index)

In [152]:
bus_locations = one_rawnav_run.loc[:,['lat','long']].apply(lambda x: [x['lat'],x['long']], axis=1).tolist()

In [153]:
# one_rawnav_run_pts = one_rawnav_run[['lat','long','door_state','veh_state','sec_past_st','geometry']].to_json()
# pt_dict = json.loads(one_rawnav_run[['lat','long','door_state','veh_state','sec_past_st','geometry']].to_json())
# pt_dict['crs'] = { "type": "name", "properties": { "name": "urn:ogc:def:crs:OGC:1.3:CRS84" }}

In [211]:
esri_imagery = "https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}"
esri_attribution = \
    "Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, " \
    "UPR-EGP, and the GIS User Community"
this_map = folium.Map(tiles='cartodbdark_matter', zoom_start=16, max_zoom=25, control_scale=True)
folium.TileLayer(name="EsriImagery", tiles=esri_imagery, attr=esri_attribution,
                 zoom_start=16, max_zoom=25, control_scale=True).add_to(this_map)
folium.TileLayer('cartodbpositron', zoom_start=16, max_zoom=20, control_scale=True).add_to(this_map)
folium.TileLayer('openstreetmap', zoom_start=16, max_zoom=20, control_scale=True).add_to(this_map)

In [212]:
this_map.fit_bounds(bus_locations)

In [213]:
h = folium.FeatureGroup(name='bus locations')

In [214]:
wr.plot_marker_clusters(this_map, one_rawnav_run, "lat","long",h)

In [215]:
# h.add_children(MarkerCluster(locations=bus_locations))

In [216]:
this_map.add_children(h)

# make bus_location index

In [187]:
one_rawnav_run.crs

<Projected CRS: EPSG:2248>
Name: NAD83 / Maryland (ftUS)
Axis Info [cartesian]:
- X[east]: Easting (US survey foot)
- Y[north]: Northing (US survey foot)
Area of Use:
- name: USA - Maryland
- bounds: (-79.49, 37.97, -74.97, 39.73)
Coordinate Operation:
- name: SPCS83 Maryland zone (US Survey feet)
- method: Lambert Conic Conformal (2SP)
Datum: North American Datum 1983
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

### make tree of bus locations

In [161]:
busA = np.array(list(zip(one_rawnav_run.geometry.x, one_rawnav_run.geometry.y)))
bustree = cKDTree(busA)

### find closests `from_nodes`

In [217]:
dist, idx = bustree.query(from_nodesA, k=1)

In [218]:
bus_from_nodes = pd.concat(
        [h802_from_nodes.reset_index(drop=True),
         one_rawnav_run.loc[idx,['filename', 'index_run_start', 'index_loc'
                                 , 'odom_ft', 'sec_past_st', 'lat', 'long']].reset_index(drop=True),
         pd.Series(dist, name='dist_to_nearest_point')]
    , axis=1)



In [219]:
from_node_lines = bus_from_nodes.copy()

In [220]:
from_node_lines.loc[:,'geometry'] = from_node_lines.loc[:,
                                                        ['FROM_LATITUDE','FROM_LONGITUDE'
                                                          ,'lat','long']].apply(
                                                    lambda x: LineString([Point(x['long'],x['lat'])
                                                  ,Point(x['FROM_LONGITUDE'],x['FROM_LATITUDE'])])
                                                , axis=1)

In [221]:
from_nodes = folium.FeatureGroup(name='from node lines')

In [222]:
from_node_lines_geo = gpd.GeoDataFrame(from_node_lines, crs="EPSG:4326",geometry='geometry')

In [223]:
folium.Choropleth(
    from_node_lines_geo,
    line_weight=3,
    line_color='red'
).add_to(this_map)

In [232]:
folium.Choropleth(
    stop_index_line,
    line_weight=3,
    line_color='orange'
).add_to(this_map)

In [233]:
this_map